In [371]:
import yfinance as yf
import pandas as pd
import numpy
import math
import altair as alt
import time
import json
import datetime
import random
import defs
import time
import datetime

#missing
#fees
#dividends
#stocksplits - what happens in  a stock split(are old shares amount converted to new share amount)


## File Load

- Load File
- Get All Distinct Stokcs
- Get All Distinct Currencies

In [393]:
filename = 'Finance_Positions.csv'


f = open(filename, "r")


count_comma=0
count_semicolon=0
for i in range(2):
    line = f.readline()
    count_comma=count_comma+line.count(",")
    count_semicolon=count_semicolon+line.count(";")


f.close()

print("Importing Transactions")

sep=","
if(count_semicolon>count_comma):
    sep=";"

#format must be dDD-MM-YYYY
transactions = pd.read_csv(filename,sep=sep,dayfirst=True)

#get the most earliest date
df=pd.DataFrame()
df['Date']=pd.to_datetime(transactions['When'],dayfirst=True)
startdate=min(df['Date']).strftime("%Y-%m-%d")

#get all use tickers distinct
stonks=pd.unique(transactions['Ticker']).tolist()

#get all distinct currencies
stonk_currencies=pd.unique(transactions['Currency']).tolist()

print("Transactions Loaded")

#transactions



Importing Transactions
Transactions Loaded


In [394]:
startdate

'2020-01-09'

In [395]:
transactions[transactions['Ticker']=='NVDA']['When'].values[0]

'12/10/2020'

In [396]:
#donwload all data
data = yf.download(tickers=stonks,start=startdate,interval='1d',group_by='column',prepos=False,threads=True)

#counts entries without values
empty_stocks  =data['Close'].columns[data['Close'].count()==0].to_list()

if len(empty_stocks)>0:
    payload= {}
    payload['stocks'] = empty_stocks
    print("WARNING: The Following Tickers are Invalid: "+" , ".join(empty_stocks)+" , tickers must be set accordingly to  https://finance.yahoo.com/",payload,status='ERROR')

print("Stock Values Loaded")


[*********************100%***********************]  42 of 42 completed
Stock Values Loaded


[*********************100%***********************]  1 of 1 completed


Timestamp('2021-05-28 00:00:00')

In [399]:

#analyse which pairs to take and downlaod
allcurrencies=[]

for ticker in stonk_currencies:
    allcurrencies.append(ticker)
    

curs = set(allcurrencies).difference(('USD',))
print(curs)

curpairs=[]

#always converts to dollars
#targetcurrency='USD'

#generate strings
for i in curs:
    curpairs.append(i+"USD=X")


#download required pairs
historicalcurrency = yf.download(tickers=curpairs,start=startdate,interval='1d',group_by='column',prepos=False,threads=True)


#targetpair = yf.download(tickers=targetcurrency+"=X",start=startdate,interval='1d',group_by='column',prepos=False,threads=True)


#Sets to  target currency
historicalcurrency=historicalcurrency['Close']#.mul(targetpair['Close'],axis=0)

{'EUR', 'GBP'}
[*********************100%***********************]  2 of 2 completed


In [400]:
historicalcurrency

EURUSD=X  GBPUSD=X
Date                          
2020-01-09  1.111321  1.310513
2020-01-10  1.111111  1.307019
2020-01-13  1.111667  1.304563
2020-01-14  1.113573  1.298819
2020-01-15  1.113090  1.302253
...              ...       ...
2021-05-25  1.221464  1.415609
2021-05-26  1.224909  1.414387
2021-05-27  1.219260  1.411612
2021-05-28  1.219319  1.420374
2021-05-31  1.219066  1.417555

[363 rows x 2 columns]

In [401]:
startdate

'2020-01-09'

In [402]:
#For every stock,get current format
curtime=datetime.datetime.now().isoformat()

#this may take a while

stonks_info={}
dividends={}

inf=0
#serial
for i in stonks:
    try:

        inf=ticker=  yf.Ticker(i).get_info()#defs.FetchTickerInfo(i)
        dividends[i]= yf.Ticker(i).dividends
    except Exception as e:
        print(e)
    stonks_info[i]=inf

    #print(i)
    


In [403]:

#yf.Ticker("PG").actions
#data['Close']['AAPL'].iloc[data['Close']['AAPL'].index>pd.to_datetime('2020-08-26')]

stonks_info['DIOD']['currency']

'USD'

In [404]:
stonkdict={}



#initialize final datafraem
superdf =pd.DataFrame()
superdf.empty

i=0


for stonk in stonks:  
    
    print(stonk)
    
    #get transactions from csv
    singlestock_transactions = transactions[transactions['Ticker']==stonk]

    #use index to create df
    index = data.index
    df=pd.DataFrame(index=data.index)

    
    #extract price
    df['Price']= data['Close'][stonk]
    #initialize amount
    df["SharesOwned"]=0
    #initialize total value
    df['TotalValue']=0  
    
    

    df['InvestedValue']=0   

    #set ticker
    df["Ticker"]=stonk
    
    #fetch currency
    df["Currency"]=stonks_info[stonk]['currency']
    if(stonk=='NVDA'):
        print(df.index.max())


    for idx, row in singlestock_transactions.iterrows():

        multiplier = 1
        if(row['What']=='buy'):
            multiplier=1
        elif(row['What']=='sell'):
            multiplier=-1
        else:
            raise Exception("Transaction \"row['What']\" is not recognized")

        #print(row['Amount'])


        #CHECK IF IT GETS APPLIED TO STARTING ARRAY, FIND AWAY TO DO THIS AT THE START
        #CONVERTING INTO AMOUNT MAKES it be adimensional, and doenst matter what currency it was bought in
        try:
            if(math.isnan(float(row['Amount']))):
                row['Amount']=row['Total Cost']/row['Cost per Share']
        except:
            row['Amount']=row['Total Cost']/row['Cost per Share']


        #df[row['When']:][stonk+" Amount"] = df[row['When']:][stonk+" Amount"]=row['Amount']

        #df[row['When']:,stonk+" Amount"] = df[row['When']:,stonk+" Amount"]+row['Amount']

        #print(float(row['Amount']))
        
        wheny = pd.to_datetime(row['When'], dayfirst=True)
        
        if pd.to_datetime("now")< wheny:
            print(row['When'],"<- This date is in the future, and will not be considere")
            continue


        
        #print(float(row['Amount'])*multiplier)
        #set amount to the amount
        #display(row['When'])
        #display(df.loc[row['When']:])
        if(stonk=='NVDA'):
            print(df.index.max())
        
        
        
        
        #change the amount from whtn to forward,  multiplier determinex if its a  buy of a sell
        df.loc[wheny:,'SharesOwned'] = df.loc[wheny:,'SharesOwned'] + (float(row['Amount'])*multiplier)

        #money put in
        df.loc[wheny:,'InvestedValue'] = df.loc[wheny:,'InvestedValue'] + (float(row['Total Cost'])*multiplier)
        
        
        
        

        

    i=i+1
        
    df.loc[:,'TotalValue']= df["Price"]*df['SharesOwned']
    df.loc[:,'EarnedValue']= df.loc[:,'TotalValue']-df.loc[:,'InvestedValue']
    
    
        
    
    
    
    
    #delete rows with no data
    #
    df.interpolate(inplace=True)
    df.dropna(inplace=True,how='any')
    
    
    #display(df)
    #display(df)
    
    
    
    superdf= superdf.append(df)
    #display(df)
    #display(superdf)
    #print("YIKES")

    




PEP


KeyError: 'PEP'

In [384]:
#Check if something is wrong
#for every stock
for stonk in stonks:  
    a = superdf.loc[superdf['Ticker']==stonk]


    if a.loc[a.index.min(),'EarnedValue']>0:
        print('Verify if Stock % has the correct date')




In [386]:
superdf.loc[superdf['Ticker']=='NVDA']

Price  SharesOwned  TotalValue  InvestedValue Ticker  \
Date                                                                    
2020-01-09  243.020004          0.0    0.000000           0.00   NVDA   
2020-01-10  244.320007          0.0    0.000000           0.00   NVDA   
2020-01-11  246.873337          0.0    0.000000           0.00   NVDA   
2020-01-12  249.426666          0.0    0.000000           0.00   NVDA   
2020-01-13  251.979996          0.0    0.000000           0.00   NVDA   
...                ...          ...         ...            ...    ...   
2021-05-26  628.000000          1.0  628.000000         571.11   NVDA   
2021-05-27  619.520020          1.0  619.520020         571.11   NVDA   
2021-05-28  649.780029          1.0  649.780029         571.11   NVDA   
2021-05-29  649.780029          1.0  649.780029         571.11   NVDA   
2021-05-31  649.780029          1.0  649.780029         571.11   NVDA   

           Currency  EarnedValue  
Date                              
2020-01-09      USD     0.000000  
2020-01-10      USD     0.000000  
2020-01-11      USD     0.000000  
2020-01-12      USD     0.000000  
2020-01-13      USD     0.000000  
...             ...          ...  
2021-05-26      USD    56.890000  
2021-05-27      USD    48.410020  
2021-05-28      USD    78.670029  
2021-05-29      USD    78.670029  
2021-05-31      USD    78.670029  

[508 rows x 7 columns]

In [353]:
#reset indexes
superdf=superdf.reset_index()


In [354]:

#calculate dividends
superdf['Dividends']=0

#for every stock
for stonk in stonks:  
    #print(stonk)
    #stonk="PEP"
    divs=dividends[stonk]

      

    #fetches the start date,crop dividends before that
    divs = divs[startdate:]


    for date, divi in divs.iteritems():

        
        #shares owned when dividends ocurred
        #filter  by stonk and date. fetch values[0]
        sharesOwned = superdf.loc[(superdf['Ticker']==stonk) & (superdf['Date']==date),'SharesOwned'].values[0]

        #debug
        if( stonk=='NVDA'):
            print(date, divi)
            print(sharesOwned)
        #print(date,row)        
        
        #if the dividend date is greater than the date,
        superdf.loc[ (superdf['Date']>=date) & (superdf['Ticker']==stonk),'Dividends']=superdf.loc[ (superdf['Date']>=date) & (superdf['Ticker']==stonk),'Dividends']  + (float(divi)*sharesOwned)
        #display(superdf.loc[superdf["Ticker"]==stonk,'Dividends'].loc[date:])
    

2020-02-27 00:00:00 0.16
0.0
2020-06-04 00:00:00 0.16
0.0
2020-09-01 00:00:00 0.16
0.0
2020-12-03 00:00:00 0.16
1.0
2021-03-09 00:00:00 0.16
1.0


In [355]:
superdf[superdf['Ticker']=='NVDA']

sharesOwned = superdf.loc[(superdf['Ticker']=='NVDA') & (superdf['Date']=='2020-02-27'),'SharesOwned']

#sharesOwned.values[0]

In [356]:

#needs index to work apparently
superdf = superdf.reset_index(drop=True).set_index(['Date'])

In [357]:
hm=superdf
hm

Price  SharesOwned  TotalValue  InvestedValue Ticker  \
Date                                                                    
2020-01-09  134.789993          0.0    0.000000           0.00    PEP   
2020-01-10  134.529999          0.0    0.000000           0.00    PEP   
2020-01-11  135.196665          0.0    0.000000           0.00    PEP   
2020-01-12  135.863332          0.0    0.000000           0.00    PEP   
2020-01-13  136.529999          0.0    0.000000           0.00    PEP   
...                ...          ...         ...            ...    ...   
2021-05-26   96.239998          2.0  192.479996         177.62      U   
2021-05-27   95.800003          2.0  191.600006         177.62      U   
2021-05-28   94.459999          2.0  188.919998         177.62      U   
2021-05-29   94.459999          2.0  188.919998         177.62      U   
2021-05-31   94.459999          2.0  188.919998         177.62      U   

           Currency  EarnedValue  Dividends  
Date                                         
2020-01-09      USD     0.000000        0.0  
2020-01-10      USD     0.000000        0.0  
2020-01-11      USD     0.000000        0.0  
2020-01-12      USD     0.000000        0.0  
2020-01-13      USD     0.000000        0.0  
...             ...          ...        ...  
2021-05-26      USD    14.859996        0.0  
2021-05-27      USD    13.980006        0.0  
2021-05-28      USD    11.299998        0.0  
2021-05-29      USD    11.299998        0.0  
2021-05-31      USD    11.299998        0.0  

[20357 rows x 8 columns]

In [358]:


#perform left join on Date field, 

superdf = pd.merge(
    hm,
    historicalcurrency,
    how="left",
    left_on='Date',
    right_on='Date',
    left_index=False,
    right_index=False,
    suffixes=("", ""),
    copy=True,
    indicator=False,
    validate=None,
)

#for every different currencu
for (cur,curp) in zip(curs,curpairs):
    #print(cur,curp)
    #interpolate missing data for currency
    superdf[curp]=superdf[curp].interpolate(method='pad')
    
    #convert Everything to USD
    superdf.loc[superdf['Currency']==cur,'TotalValue'] = superdf[superdf['Currency']==cur]['TotalValue']*superdf[superdf['Currency']==cur][curp]
    superdf.loc[superdf['Currency']==cur,'InvestedValue'] = superdf[superdf['Currency']==cur]['InvestedValue']*superdf[superdf['Currency']==cur][curp]
    superdf.loc[superdf['Currency']==cur,'EarnedValue'] = superdf[superdf['Currency']==cur]['EarnedValue']*superdf[superdf['Currency']==cur][curp]
    superdf.loc[superdf['Currency']==cur,'Dividends'] = superdf[superdf['Currency']==cur]['Dividends']*superdf[superdf['Currency']==cur][curp]
   


In [359]:
superdf

Price  SharesOwned  TotalValue  InvestedValue Ticker  \
Date                                                                    
2020-01-09  134.789993          0.0    0.000000           0.00    PEP   
2020-01-10  134.529999          0.0    0.000000           0.00    PEP   
2020-01-11  135.196665          0.0    0.000000           0.00    PEP   
2020-01-12  135.863332          0.0    0.000000           0.00    PEP   
2020-01-13  136.529999          0.0    0.000000           0.00    PEP   
...                ...          ...         ...            ...    ...   
2021-05-26   96.239998          2.0  192.479996         177.62      U   
2021-05-27   95.800003          2.0  191.600006         177.62      U   
2021-05-28   94.459999          2.0  188.919998         177.62      U   
2021-05-29   94.459999          2.0  188.919998         177.62      U   
2021-05-31   94.459999          2.0  188.919998         177.62      U   

           Currency  EarnedValue  Dividends  EURUSD=X  GBPUSD=X  
Date                                                             
2020-01-09      USD     0.000000        0.0  1.111321  1.310513  
2020-01-10      USD     0.000000        0.0  1.111111  1.307019  
2020-01-11      USD     0.000000        0.0  1.111111  1.307019  
2020-01-12      USD     0.000000        0.0  1.111111  1.307019  
2020-01-13      USD     0.000000        0.0  1.111667  1.304563  
...             ...          ...        ...       ...       ...  
2021-05-26      USD    14.859996        0.0  1.224909  1.414387  
2021-05-27      USD    13.980006        0.0  1.219260  1.411612  
2021-05-28      USD    11.299998        0.0  1.219319  1.420374  
2021-05-29      USD    11.299998        0.0  1.219319  1.420374  
2021-05-31      USD    11.299998        0.0  1.219810  1.417917  

[20357 rows x 10 columns]

In [360]:
#superdf[superdf['Ticker']=='XOM']
dfforaltair = superdf.reset_index()
dfforaltair.interpolate(inplace=True)

alt.data_transformers.disable_max_rows()
alt.Chart(dfforaltair).mark_area().encode(
    x='Date',
    y='InvestedValue',
    #color='Ticker:N',
    color=alt.Color('Ticker:N', legend=alt.Legend(columns=1,symbolLimit=300)),
).properties(
    width=1280,
    height=720
)

alt.Chart(...)

In [361]:
superdf.to_csv('PorfolioHistory.csv')

In [305]:
## Drill down

superdf[superdf['Ticker']=='NVDA']

Price  SharesOwned  TotalValue  InvestedValue Ticker  \
Date                                                                    
2020-01-09  243.020004          0.0    0.000000           0.00   NVDA   
2020-01-10  244.320007          0.0    0.000000           0.00   NVDA   
2020-01-11  246.873337          0.0    0.000000           0.00   NVDA   
2020-01-12  249.426666          0.0    0.000000           0.00   NVDA   
2020-01-13  251.979996          0.0    0.000000           0.00   NVDA   
...                ...          ...         ...            ...    ...   
2021-05-26  628.000000          1.0  628.000000         571.11   NVDA   
2021-05-27  619.520020          1.0  619.520020         571.11   NVDA   
2021-05-28  649.780029          1.0  649.780029         571.11   NVDA   
2021-05-29  649.780029          1.0  649.780029         571.11   NVDA   
2021-05-31  649.780029          1.0  649.780029         571.11   NVDA   

           Currency  EarnedValue  Dividends  EURUSD=X  GBPUSD=X  
Date                                                             
2020-01-09      USD     0.000000       0.00  1.111321  1.310513  
2020-01-10      USD     0.000000       0.00  1.111111  1.307019  
2020-01-11      USD     0.000000       0.00  1.111111  1.307019  
2020-01-12      USD     0.000000       0.00  1.111111  1.307019  
2020-01-13      USD     0.000000       0.00  1.111667  1.304563  
...             ...          ...        ...       ...       ...  
2021-05-26      USD    56.890000       0.32  1.224909  1.414387  
2021-05-27      USD    48.410020       0.32  1.219260  1.411612  
2021-05-28      USD    78.670029       0.32  1.219319  1.420374  
2021-05-29      USD    78.670029       0.32  1.219319  1.420374  
2021-05-31      USD    78.670029       0.32  1.219810  1.418661  

[508 rows x 10 columns]

In [306]:
superdf

Price  SharesOwned  TotalValue  InvestedValue Ticker  \
Date                                                                    
2020-01-09  134.789993          0.0    0.000000           0.00    PEP   
2020-01-10  134.529999          0.0    0.000000           0.00    PEP   
2020-01-11  135.196665          0.0    0.000000           0.00    PEP   
2020-01-12  135.863332          0.0    0.000000           0.00    PEP   
2020-01-13  136.529999          0.0    0.000000           0.00    PEP   
...                ...          ...         ...            ...    ...   
2021-05-26   96.239998          2.0  192.479996         177.62      U   
2021-05-27   95.800003          2.0  191.600006         177.62      U   
2021-05-28   94.459999          2.0  188.919998         177.62      U   
2021-05-29   94.459999          2.0  188.919998         177.62      U   
2021-05-31   94.459999          2.0  188.919998         177.62      U   

           Currency  EarnedValue  Dividends  EURUSD=X  GBPUSD=X  
Date                                                             
2020-01-09      USD     0.000000        0.0  1.111321  1.310513  
2020-01-10      USD     0.000000        0.0  1.111111  1.307019  
2020-01-11      USD     0.000000        0.0  1.111111  1.307019  
2020-01-12      USD     0.000000        0.0  1.111111  1.307019  
2020-01-13      USD     0.000000        0.0  1.111667  1.304563  
...             ...          ...        ...       ...       ...  
2021-05-26      USD    14.859996        0.0  1.224909  1.414387  
2021-05-27      USD    13.980006        0.0  1.219260  1.411612  
2021-05-28      USD    11.299998        0.0  1.219319  1.420374  
2021-05-29      USD    11.299998        0.0  1.219319  1.420374  
2021-05-31      USD    11.299998        0.0  1.219810  1.418661  

[20357 rows x 10 columns]

In [307]:
dividends['NVDA']

Date
2012-11-20    0.075
2013-02-26    0.075
2013-05-21    0.075
2013-08-20    0.075
2013-11-19    0.085
2014-02-25    0.085
2014-05-20    0.085
2014-08-19    0.085
2014-11-19    0.085
2015-02-24    0.085
2015-05-19    0.098
2015-08-18    0.098
2015-11-18    0.115
2016-02-29    0.115
2016-05-24    0.115
2016-08-23    0.115
2016-11-23    0.140
2017-02-22    0.140
2017-05-19    0.140
2017-08-22    0.140
2017-11-22    0.150
2018-02-22    0.150
2018-05-23    0.150
2018-08-29    0.150
2018-11-29    0.160
2019-02-28    0.160
2019-05-30    0.160
2019-08-28    0.160
2019-11-27    0.160
2020-02-27    0.160
2020-06-04    0.160
2020-09-01    0.160
2020-12-03    0.160
2021-03-09    0.160
Name: Dividends, dtype: float64

In [308]:
superdf[superdf['Ticker']=='PEP']

Price  SharesOwned  TotalValue  InvestedValue Ticker  \
Date                                                                    
2020-01-09  134.789993          0.0    0.000000           0.00    PEP   
2020-01-10  134.529999          0.0    0.000000           0.00    PEP   
2020-01-11  135.196665          0.0    0.000000           0.00    PEP   
2020-01-12  135.863332          0.0    0.000000           0.00    PEP   
2020-01-13  136.529999          0.0    0.000000           0.00    PEP   
...                ...          ...         ...            ...    ...   
2021-05-26  148.300003          3.0  444.900009         438.56    PEP   
2021-05-27  146.509995          3.0  439.529984         438.56    PEP   
2021-05-28  147.940002          3.0  443.820007         438.56    PEP   
2021-05-29  147.940002          3.0  443.820007         438.56    PEP   
2021-05-31  147.940002          3.0  443.820007         438.56    PEP   

           Currency  EarnedValue  Dividends  EURUSD=X  GBPUSD=X  
Date                                                             
2020-01-09      USD     0.000000      0.000  1.111321  1.310513  
2020-01-10      USD     0.000000      0.000  1.111111  1.307019  
2020-01-11      USD     0.000000      0.000  1.111111  1.307019  
2020-01-12      USD     0.000000      0.000  1.111111  1.307019  
2020-01-13      USD     0.000000      0.000  1.111667  1.304563  
...             ...          ...        ...       ...       ...  
2021-05-26      USD     6.340009      3.069  1.224909  1.414387  
2021-05-27      USD     0.969984      3.069  1.219260  1.411612  
2021-05-28      USD     5.260007      3.069  1.219319  1.420374  
2021-05-29      USD     5.260007      3.069  1.219319  1.420374  
2021-05-31      USD     5.260007      3.069  1.219810  1.418661  

[508 rows x 10 columns]

In [309]:
superdf

Price  SharesOwned  TotalValue  InvestedValue Ticker  \
Date                                                                    
2020-01-09  134.789993          0.0    0.000000           0.00    PEP   
2020-01-10  134.529999          0.0    0.000000           0.00    PEP   
2020-01-11  135.196665          0.0    0.000000           0.00    PEP   
2020-01-12  135.863332          0.0    0.000000           0.00    PEP   
2020-01-13  136.529999          0.0    0.000000           0.00    PEP   
...                ...          ...         ...            ...    ...   
2021-05-26   96.239998          2.0  192.479996         177.62      U   
2021-05-27   95.800003          2.0  191.600006         177.62      U   
2021-05-28   94.459999          2.0  188.919998         177.62      U   
2021-05-29   94.459999          2.0  188.919998         177.62      U   
2021-05-31   94.459999          2.0  188.919998         177.62      U   

           Currency  EarnedValue  Dividends  EURUSD=X  GBPUSD=X  
Date                                                             
2020-01-09      USD     0.000000        0.0  1.111321  1.310513  
2020-01-10      USD     0.000000        0.0  1.111111  1.307019  
2020-01-11      USD     0.000000        0.0  1.111111  1.307019  
2020-01-12      USD     0.000000        0.0  1.111111  1.307019  
2020-01-13      USD     0.000000        0.0  1.111667  1.304563  
...             ...          ...        ...       ...       ...  
2021-05-26      USD    14.859996        0.0  1.224909  1.414387  
2021-05-27      USD    13.980006        0.0  1.219260  1.411612  
2021-05-28      USD    11.299998        0.0  1.219319  1.420374  
2021-05-29      USD    11.299998        0.0  1.219319  1.420374  
2021-05-31      USD    11.299998        0.0  1.219810  1.418661  

[20357 rows x 10 columns]

In [ ]:

#for every stock
for stonk in stonks:  
    print(stonk)
    #stonk="PEP"
    divs=dividends[stonk]

      

    #fetches the start date,crop dividends before that
    divs = divs[startdate:]


    for date, divi in divs.iteritems():

        
        #shares owned when dividends ocurred
        #filter  by stonk and date. fetch values[0]
        sharesOwned = superdf.loc[(superdf['Ticker']==stonk) & (superdf['Date']==date),'SharesOwned'].values[0]

        #debug
        if( stonk=='NVDA'):
            print(date, divi)
            print(sharesOwned)
        #print(date,row)        
        
        #if the dividend date is greater than the date,
        superdf.loc[ (superdf['Date']>=date) & (superdf['Ticker']==stonk),'Dividends']=superdf.loc[ (superdf['Date']>=date) & (superdf['Ticker']==stonk),'Dividends']  + (float(divi)*sharesOwned)
        #display(superdf.loc[superdf["Ticker"]==stonk,'Dividends'].loc[date:])
    

In [ ]:
stok = 'PEP'

min(df.loc[]['Date']).strftime("%Y-%m-%d")

Timestamp('2020-01-09 00:00:00')